In [1]:
!pip install pycaret

     |████████████████████████████████| 301 kB 4.0 MB/s 
     |████████████████████████████████| 167 kB 30.9 MB/s 
     |████████████████████████████████| 15.6 MB 794 kB/s 
     |████████████████████████████████| 86 kB 6.2 MB/s 
     |████████████████████████████████| 114 kB 39.1 MB/s 
     |████████████████████████████████| 261 kB 45.2 MB/s 
     |████████████████████████████████| 6.8 MB 34.9 MB/s 
     |████████████████████████████████| 56 kB 4.6 MB/s 
     |████████████████████████████████| 1.7 MB 35.4 MB/s 
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Installing backend dependencies ... done
    Preparing wheel metadata ... done
     |████████████████████████████████| 1.3 MB 34.2 MB/s 
     |████████████████████████████████| 2.0 MB 31.9 MB/s 
     |████████████████████████████████| 274 kB 46.5 MB/s 
     |████████████████████████████████| 636 kB 45.0 MB/s 
     |████████████████████████████████| 102 kB 13.1 MB/s 
     |██████████████████

In [1]:
!pip install pandas_profiling

In [1]:
#For Google Colab only
from pycaret.utils import enable_colab 
enable_colab()

Colab mode enabled.


In [2]:
# Import the necessarry libraries
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import itertools
import pycaret
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.neighbors import KNeighborsClassifier
from sklearn.naive_bayes import GaussianNB
from sklearn.linear_model import LogisticRegression
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis
from sklearn.naive_bayes import GaussianNB
from sklearn.metrics import silhouette_samples, silhouette_score
from sklearn.metrics import confusion_matrix,classification_report,roc_auc_score,accuracy_score,roc_auc_score,roc_curve, precision_score, recall_score, f1_score
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import cross_validate
from scipy.stats import zscore
from sklearn.ensemble import RandomForestClassifier
from sklearn.ensemble import AdaBoostClassifier
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.model_selection import cross_val_score
from sklearn import svm
import xgboost as xgb
from sklearn.ensemble import BaggingClassifier
from imblearn.over_sampling import SMOTE
import warnings
from scipy.stats import zscore
warnings.filterwarnings("ignore")
import pandas_profiling as pp

In [3]:
# Load the dataset
shinkasen_train_df = pd.read_csv('/content/drive/MyDrive/PGP-DSBA/Hackathon/Shinkasen/Traveldata_train.csv')
shinkasen_train_df.head()

ID  Gender  ... DepartureDelay_in_Mins  ArrivalDelay_in_Mins
0  98800001  Female  ...                    0.0                   5.0
1  98800002    Male  ...                    9.0                   0.0
2  98800003  Female  ...                   77.0                 119.0
3  98800004  Female  ...                   13.0                  18.0
4  98800005  Female  ...                    0.0                   0.0

[5 rows x 9 columns]

In [4]:
# Load the dataset
shinkasen_survey_train_df = pd.read_csv('/content/drive/MyDrive/PGP-DSBA/Hackathon/Shinkasen/Surveydata_train.csv')
shinkasen_survey_train_df.head()

ID  Overall_Experience  ...       Cleanliness Online_boarding
0  98800001                   0  ...  need improvement            poor
1  98800002                   0  ...              good            good
2  98800003                   1  ...         excellent       excellent
3  98800004                   0  ...        acceptable      acceptable
4  98800005                   1  ...              good            good

[5 rows x 17 columns]

In [5]:
# Combine the two data frames

train_df = shinkasen_train_df.merge(shinkasen_survey_train_df, on='ID')
train_df.head()

ID  Gender  ...       Cleanliness  Online_boarding
0  98800001  Female  ...  need improvement             poor
1  98800002    Male  ...              good             good
2  98800003  Female  ...         excellent        excellent
3  98800004  Female  ...        acceptable       acceptable
4  98800005  Female  ...              good             good

[5 rows x 25 columns]

In [6]:
# Load the test dataset
shinkasen_test_df = pd.read_csv('/content/drive/MyDrive/PGP-DSBA/Hackathon/Shinkasen/Traveldata_test.csv')
shinkasen_test_df.head()

ID  Gender  ... DepartureDelay_in_Mins  ArrivalDelay_in_Mins
0  99900001  Female  ...                    0.0                   0.0
1  99900002  Female  ...                    9.0                  28.0
2  99900003    Male  ...                    0.0                   0.0
3  99900004  Female  ...                    0.0                   0.0
4  99900005    Male  ...                   17.0                   0.0

[5 rows x 9 columns]

In [7]:
# Load the dataset
shinkasen_survey_test_df = pd.read_csv('/content/drive/MyDrive/PGP-DSBA/Hackathon/Shinkasen/Surveydata_test.csv')
shinkasen_survey_test_df.head()

ID    Seat_comfort  ...       Cleanliness Online_boarding
0  99900001      acceptable  ...         excellent            poor
1  99900002  extremely poor  ...         excellent      acceptable
2  99900003       excellent  ...  need improvement       excellent
3  99900004      acceptable  ...         excellent            poor
4  99900005       excellent  ...         excellent       excellent

[5 rows x 16 columns]

In [8]:
# Combine the two data frames

test_df = shinkasen_test_df.merge(shinkasen_survey_test_df, on='ID')
test_df.head()

ID  Gender  ...       Cleanliness  Online_boarding
0  99900001  Female  ...         excellent             poor
1  99900002  Female  ...         excellent       acceptable
2  99900003    Male  ...  need improvement        excellent
3  99900004  Female  ...         excellent             poor
4  99900005    Male  ...         excellent        excellent

[5 rows x 24 columns]

In [9]:
train_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 94379 entries, 0 to 94378
Data columns (total 25 columns):
 #   Column                   Non-Null Count  Dtype  
---  ------                   --------------  -----  
 0   ID                       94379 non-null  int64  
 1   Gender                   94302 non-null  object 
 2   CustomerType             85428 non-null  object 
 3   Age                      94346 non-null  float64
 4   TypeTravel               85153 non-null  object 
 5   Travel_Class             94379 non-null  object 
 6   Travel_Distance          94379 non-null  int64  
 7   DepartureDelay_in_Mins   94322 non-null  float64
 8   ArrivalDelay_in_Mins     94022 non-null  float64
 9   Overall_Experience       94379 non-null  int64  
 10  Seat_comfort             94318 non-null  object 
 11  Seat_Class               94379 non-null  object 
 12  Arrival_time_convenient  85449 non-null  object 
 13  Catering                 85638 non-null  object 
 14  Platform_location     

In [12]:
profile = pp.ProfileReport(train_df)
profile

Output hidden; open in https://colab.research.google.com to view.

In [11]:
data = train_df.copy()
data_unseen = test_df.copy()
data.reset_index(inplace=True, drop=True)
print('Data for Modeling: ' + str(data.shape))
print('Unseen Data For Predictions: ' + str(data_unseen.shape))

Data for Modeling: (94379, 25)
Unseen Data For Predictions: (35602, 24)


In [13]:
from pycaret.classification import *

In [17]:
numeric_cols = train_df.select_dtypes(exclude= 'object').columns.to_list()
numeric_cols

['ID',
 'Age',
 'Travel_Distance',
 'DepartureDelay_in_Mins',
 'ArrivalDelay_in_Mins',
 'Overall_Experience']

In [18]:
categorical_cols = train_df.select_dtypes('object').columns.to_list()
categorical_cols

['Gender',
 'CustomerType',
 'TypeTravel',
 'Travel_Class',
 'Seat_comfort',
 'Seat_Class',
 'Arrival_time_convenient',
 'Catering',
 'Platform_location',
 'Onboardwifi_service',
 'Onboard_entertainment',
 'Online_support',
 'Onlinebooking_Ease',
 'Onboard_service',
 'Leg_room',
 'Baggage_handling',
 'Checkin_service',
 'Cleanliness',
 'Online_boarding']

In [42]:
shinkasen_clf = setup(data = data, target = 'Overall_Experience', ignore_features = ['ID'], 
               imputation_type = 'simple', numeric_imputation = 'mean', categorical_imputation = 'mode', 
               handle_unknown_categorical = True, unknown_categorical_method = 'most_frequent', remove_outliers = True,normalize = True, 
               remove_multicollinearity = True, multicollinearity_threshold = 0.6, use_gpu = True, fold=5,
               session_id=123)

Description               Value
0                               session_id                 123
1                                   Target  Overall_Experience
2                              Target Type              Binary
3                            Label Encoded                None
4                            Original Data         (94379, 25)
5                           Missing Values                True
6                         Numeric Features                   4
7                     Categorical Features                  19
8                         Ordinal Features               False
9                High Cardinality Features               False
10                 High Cardinality Method                None
11                   Transformed Train Set         (62761, 71)
12                    Transformed Test Set         (28314, 71)
13                      Shuffle Train-Test                True
14                     Stratify Train-Test               False
15                          Fold Generator     StratifiedKFold
16                             Fold Number                   5
17                                CPU Jobs                  -1
18                                 Use GPU                True
19                          Log Experiment               False
20                         Experiment Name    clf-default-name
21                                     USI                2c23
22                         Imputation Type              simple
23          Iterative Imputation Iteration                None
24                         Numeric Imputer                mean
25      Iterative Imputation Numeric Model                None
26                     Categorical Imputer                mode
27  Iterative Imputation Categorical Model                None
28           Unknown Categoricals Handling       most_frequent
29                               Normalize                True
30                        Normalize Method              zscore
31                          Transformation               False
32                   Transformation Method                None
33                                     PCA               False
34                              PCA Method                None
35                          PCA Components                None
36                     Ignore Low Variance               False
37                     Combine Rare Levels               False
38                    Rare Level Threshold                None
39                         Numeric Binning               False
40                         Remove Outliers                True
41                      Outliers Threshold                0.05
42                Remove Multicollinearity                True
43             Multicollinearity Threshold                 0.6
44             Remove Perfect Collinearity                True
45                              Clustering               False
46                    Clustering Iteration                None
47                     Polynomial Features               False
48                       Polynomial Degree                None
49                    Trignometry Features               False
50                    Polynomial Threshold                None
51                          Group Features               False
52                       Feature Selection               False
53                Feature Selection Method             classic
54            Features Selection Threshold                None
55                     Feature Interaction               False
56                           Feature Ratio               False
57                   Interaction Threshold                None
58                           Fix Imbalance               False
59                    Fix Imbalance Method               SMOTE

In [41]:
shinkasen_clf1 = setup(data = data, target = 'Overall_Experience', ignore_features = ['ID'], 
               imputation_type = 'simple', numeric_imputation = 'mean', categorical_imputation = 'mode', 
               handle_unknown_categorical = True, unknown_categorical_method = 'most_frequent', remove_outliers = True,normalize = True, use_gpu=True, fold=5, 
               session_id=123)

Description               Value
0                               session_id                 123
1                                   Target  Overall_Experience
2                              Target Type              Binary
3                            Label Encoded                None
4                            Original Data         (94379, 25)
5                           Missing Values                True
6                         Numeric Features                   4
7                     Categorical Features                  19
8                         Ordinal Features               False
9                High Cardinality Features               False
10                 High Cardinality Method                None
11                   Transformed Train Set         (62761, 83)
12                    Transformed Test Set         (28314, 83)
13                      Shuffle Train-Test                True
14                     Stratify Train-Test               False
15                          Fold Generator     StratifiedKFold
16                             Fold Number                   5
17                                CPU Jobs                  -1
18                                 Use GPU                True
19                          Log Experiment               False
20                         Experiment Name    clf-default-name
21                                     USI                ea12
22                         Imputation Type              simple
23          Iterative Imputation Iteration                None
24                         Numeric Imputer                mean
25      Iterative Imputation Numeric Model                None
26                     Categorical Imputer                mode
27  Iterative Imputation Categorical Model                None
28           Unknown Categoricals Handling       most_frequent
29                               Normalize                True
30                        Normalize Method              zscore
31                          Transformation               False
32                   Transformation Method                None
33                                     PCA               False
34                              PCA Method                None
35                          PCA Components                None
36                     Ignore Low Variance               False
37                     Combine Rare Levels               False
38                    Rare Level Threshold                None
39                         Numeric Binning               False
40                         Remove Outliers                True
41                      Outliers Threshold                0.05
42                Remove Multicollinearity               False
43             Multicollinearity Threshold                None
44             Remove Perfect Collinearity                True
45                              Clustering               False
46                    Clustering Iteration                None
47                     Polynomial Features               False
48                       Polynomial Degree                None
49                    Trignometry Features               False
50                    Polynomial Threshold                None
51                          Group Features               False
52                       Feature Selection               False
53                Feature Selection Method             classic
54            Features Selection Threshold                None
55                     Feature Interaction               False
56                           Feature Ratio               False
57                   Interaction Threshold                None
58                           Fix Imbalance               False
59                    Fix Imbalance Method               SMOTE

In [39]:
shinkasen_clf2 = setup(data = data, target = 'Overall_Experience', ignore_features = ['ID'], 
               numeric_imputation = 'mean', categorical_imputation = 'mode', 
               handle_unknown_categorical = True, unknown_categorical_method = 'most_frequent', remove_outliers = True,normalize = True, 
               remove_multicollinearity = True, multicollinearity_threshold = 0.6, pca = True, pca_components = 10, use_gpu = True, fold =5, 
               session_id=123)

Description               Value
0                               session_id                 123
1                                   Target  Overall_Experience
2                              Target Type              Binary
3                            Label Encoded                None
4                            Original Data         (94379, 25)
5                           Missing Values                True
6                         Numeric Features                   4
7                     Categorical Features                  19
8                         Ordinal Features               False
9                High Cardinality Features               False
10                 High Cardinality Method                None
11                   Transformed Train Set         (62761, 10)
12                    Transformed Test Set         (28314, 10)
13                      Shuffle Train-Test                True
14                     Stratify Train-Test               False
15                          Fold Generator     StratifiedKFold
16                             Fold Number                   5
17                                CPU Jobs                  -1
18                                 Use GPU                True
19                          Log Experiment               False
20                         Experiment Name    clf-default-name
21                                     USI                4a49
22                         Imputation Type              simple
23          Iterative Imputation Iteration                None
24                         Numeric Imputer                mean
25      Iterative Imputation Numeric Model                None
26                     Categorical Imputer                mode
27  Iterative Imputation Categorical Model                None
28           Unknown Categoricals Handling       most_frequent
29                               Normalize                True
30                        Normalize Method              zscore
31                          Transformation               False
32                   Transformation Method                None
33                                     PCA                True
34                              PCA Method              linear
35                          PCA Components                  10
36                     Ignore Low Variance               False
37                     Combine Rare Levels               False
38                    Rare Level Threshold                None
39                         Numeric Binning               False
40                         Remove Outliers                True
41                      Outliers Threshold                0.05
42                Remove Multicollinearity                True
43             Multicollinearity Threshold                 0.6
44             Remove Perfect Collinearity                True
45                              Clustering               False
46                    Clustering Iteration                None
47                     Polynomial Features               False
48                       Polynomial Degree                None
49                    Trignometry Features               False
50                    Polynomial Threshold                None
51                          Group Features               False
52                       Feature Selection               False
53                Feature Selection Method             classic
54            Features Selection Threshold                None
55                     Feature Interaction               False
56                           Feature Ratio               False
57                   Interaction Threshold                None
58                           Fix Imbalance               False
59                    Fix Imbalance Method               SMOTE

In [40]:
shinkasen_best_model2 = compare_models()

Model  Accuracy     AUC  Recall   Prec.  \
et                 Extra Trees Classifier    0.8844  0.9543  0.8775  0.9064   
rf               Random Forest Classifier    0.8813  0.9518  0.8803  0.8988   
lightgbm  Light Gradient Boosting Machine    0.8776  0.9493  0.8760  0.8961   
knn                K Neighbors Classifier    0.8714  0.9342  0.8686  0.8916   
gbc          Gradient Boosting Classifier    0.8515  0.9263  0.8582  0.8668   
ada                  Ada Boost Classifier    0.8329  0.9100  0.8512  0.8424   
lr                    Logistic Regression    0.8261  0.9018  0.8498  0.8330   
svm                   SVM - Linear Kernel    0.8254  0.0000  0.8408  0.8381   
ridge                    Ridge Classifier    0.8227  0.0000  0.8484  0.8289   
lda          Linear Discriminant Analysis    0.8227  0.9008  0.8482  0.8290   
qda       Quadratic Discriminant Analysis    0.8166  0.8975  0.8236  0.8360   
dt               Decision Tree Classifier    0.8155  0.8140  0.8318  0.8288   
nb                            Naive Bayes    0.7996  0.8774  0.8238  0.8101   
dummy                    Dummy Classifier    0.5426  0.5000  1.0000  0.5426   

              F1   Kappa     MCC  TT (Sec)  
et        0.8917  0.7678  0.7683     8.064  
rf        0.8895  0.7613  0.7615    15.300  
lightgbm  0.8859  0.7539  0.7541     0.918  
knn       0.8799  0.7414  0.7418     4.482  
gbc       0.8625  0.7011  0.7011    20.676  
ada       0.8468  0.6630  0.6630     4.378  
lr        0.8413  0.6489  0.6491     0.178  
svm       0.8393  0.6481  0.6484     0.192  
ridge     0.8385  0.6420  0.6423     0.092  
lda       0.8385  0.6420  0.6423     0.194  
qda       0.8297  0.6310  0.6311     0.116  
dt        0.8303  0.6282  0.6282     0.946  
nb        0.8169  0.5956  0.5958     0.072  
dummy     0.7035  0.0000  0.0000     0.048

In [15]:
shinkasen_best_model = compare_models()

Model  Accuracy     AUC  Recall   Prec.  \
et                 Extra Trees Classifier    0.9498  0.9904  0.9464  0.9606   
rf               Random Forest Classifier    0.9471  0.9901  0.9429  0.9589   
lightgbm  Light Gradient Boosting Machine    0.9470  0.9909  0.9464  0.9555   
knn                K Neighbors Classifier    0.9250  0.9723  0.9260  0.9351   
dt               Decision Tree Classifier    0.9247  0.9239  0.9330  0.9285   
gbc          Gradient Boosting Classifier    0.9192  0.9774  0.9250  0.9261   
lr                    Logistic Regression    0.8981  0.9615  0.9024  0.9092   
svm                   SVM - Linear Kernel    0.8967  0.0000  0.8883  0.9188   
ada                  Ada Boost Classifier    0.8946  0.9603  0.8994  0.9057   
ridge                    Ridge Classifier    0.8919  0.0000  0.9006  0.9002   
lda          Linear Discriminant Analysis    0.8919  0.9583  0.9006  0.9003   
nb                            Naive Bayes    0.8450  0.9357  0.7517  0.9526   
qda       Quadratic Discriminant Analysis    0.5929  0.5856  0.6710  0.6128   
dummy                    Dummy Classifier    0.5426  0.5000  1.0000  0.5426   

              F1   Kappa     MCC  TT (Sec)  
et        0.9534  0.8991  0.8992     7.031  
rf        0.9508  0.8935  0.8937     6.013  
lightgbm  0.9509  0.8934  0.8934     1.021  
knn       0.9305  0.8490  0.8491   101.460  
dt        0.9308  0.8482  0.8483     0.482  
gbc       0.9255  0.8373  0.8373    10.846  
lr        0.9058  0.7949  0.7950     2.469  
svm       0.9032  0.7926  0.7932     0.365  
ada       0.9025  0.7877  0.7878     2.676  
ridge     0.9004  0.7822  0.7822     0.103  
lda       0.9004  0.7823  0.7823     0.992  
nb        0.8403  0.6937  0.7122     0.094  
qda       0.6287  0.1739  0.1843     0.489  
dummy     0.7035  0.0000  0.0000     0.049

In [43]:
shinkasen_best_model1 = compare_models()

Model  Accuracy     AUC  Recall   Prec.  \
et                 Extra Trees Classifier    0.9484  0.9901  0.9443  0.9599   
lightgbm  Light Gradient Boosting Machine    0.9469  0.9907  0.9456  0.9561   
rf               Random Forest Classifier    0.9462  0.9899  0.9415  0.9586   
knn                K Neighbors Classifier    0.9241  0.9720  0.9251  0.9343   
dt               Decision Tree Classifier    0.9238  0.9231  0.9319  0.9281   
gbc          Gradient Boosting Classifier    0.9190  0.9774  0.9243  0.9264   
lr                    Logistic Regression    0.8981  0.9616  0.9027  0.9090   
svm                   SVM - Linear Kernel    0.8976  0.0000  0.9037  0.9075   
ada                  Ada Boost Classifier    0.8940  0.9601  0.8987  0.9053   
ridge                    Ridge Classifier    0.8917  0.0000  0.9006  0.9000   
lda          Linear Discriminant Analysis    0.8917  0.9583  0.9006  0.9000   
nb                            Naive Bayes    0.8449  0.9356  0.7515  0.9526   
qda       Quadratic Discriminant Analysis    0.5518  0.5468  0.6061  0.5813   
dummy                    Dummy Classifier    0.5426  0.5000  1.0000  0.5426   

              F1   Kappa     MCC  TT (Sec)  
et        0.9520  0.8961  0.8963     9.018  
lightgbm  0.9508  0.8932  0.8933     1.112  
rf        0.9500  0.8917  0.8919     7.346  
knn       0.9297  0.8472  0.8472   166.602  
dt        0.9300  0.8465  0.8465     0.568  
gbc       0.9253  0.8369  0.8369    11.336  
lr        0.9058  0.7949  0.7950     2.500  
svm       0.9055  0.7938  0.7941     0.418  
ada       0.9020  0.7866  0.7866     3.074  
ridge     0.9003  0.7818  0.7819     0.168  
lda       0.9003  0.7819  0.7819     0.888  
nb        0.8402  0.6935  0.7120     0.122  
qda       0.5919  0.0945  0.0960     0.518  
dummy     0.7035  0.0000  0.0000     0.056

In [30]:
print(shinkasen_best_model1)

ExtraTreesClassifier(bootstrap=False, ccp_alpha=0.0, class_weight=None,
                     criterion='gini', max_depth=None, max_features='auto',
                     max_leaf_nodes=None, max_samples=None,
                     min_impurity_decrease=0.0, min_impurity_split=None,
                     min_samples_leaf=1, min_samples_split=2,
                     min_weight_fraction_leaf=0.0, n_estimators=100, n_jobs=-1,
                     oob_score=False, random_state=123, verbose=0,
                     warm_start=False)


In [17]:
shinkasen_et = create_model('et')

Accuracy     AUC  Recall   Prec.      F1   Kappa     MCC
0       0.9460  0.9894  0.9466  0.9536  0.9501  0.8913  0.8913
1       0.9514  0.9901  0.9486  0.9613  0.9549  0.9022  0.9023
2       0.9484  0.9905  0.9501  0.9546  0.9523  0.8960  0.8961
3       0.9457  0.9902  0.9419  0.9573  0.9495  0.8907  0.8908
4       0.9544  0.9914  0.9492  0.9662  0.9576  0.9083  0.9085
5       0.9535  0.9909  0.9474  0.9662  0.9567  0.9064  0.9066
6       0.9522  0.9913  0.9477  0.9636  0.9556  0.9038  0.9040
7       0.9468  0.9897  0.9436  0.9577  0.9506  0.8929  0.8930
8       0.9452  0.9882  0.9369  0.9611  0.9489  0.8898  0.8902
9       0.9547  0.9922  0.9521  0.9640  0.9581  0.9089  0.9090
Mean    0.9498  0.9904  0.9464  0.9606  0.9534  0.8991  0.8992
SD      0.0036  0.0011  0.0043  0.0043  0.0034  0.0073  0.0073

In [31]:
shinkasen_et = create_model('et')

Accuracy     AUC  Recall   Prec.      F1   Kappa     MCC
0       0.9498  0.9900  0.9492  0.9579  0.9535  0.8990  0.8990
1       0.9516  0.9903  0.9468  0.9633  0.9550  0.9026  0.9027
2       0.9530  0.9907  0.9548  0.9584  0.9566  0.9053  0.9053
3       0.9482  0.9903  0.9442  0.9597  0.9519  0.8958  0.8960
4       0.9520  0.9911  0.9480  0.9630  0.9555  0.9035  0.9036
5       0.9525  0.9912  0.9480  0.9639  0.9559  0.9045  0.9046
6       0.9541  0.9914  0.9465  0.9682  0.9572  0.9077  0.9080
7       0.9463  0.9902  0.9436  0.9568  0.9502  0.8920  0.8921
8       0.9468  0.9881  0.9363  0.9646  0.9502  0.8931  0.8935
9       0.9544  0.9923  0.9498  0.9657  0.9577  0.9083  0.9085
Mean    0.9509  0.9906  0.9467  0.9621  0.9544  0.9012  0.9013
SD      0.0028  0.0011  0.0046  0.0035  0.0026  0.0056  0.0056

In [24]:
#trained model object is stored in the variable 'dt'. 
print(shinkasen_et)

ExtraTreesClassifier(bootstrap=False, ccp_alpha=0.0, class_weight=None,
                     criterion='gini', max_depth=None, max_features='auto',
                     max_leaf_nodes=None, max_samples=None,
                     min_impurity_decrease=0.0, min_impurity_split=None,
                     min_samples_leaf=1, min_samples_split=2,
                     min_weight_fraction_leaf=0.0, n_estimators=100, n_jobs=-1,
                     oob_score=False, random_state=123, verbose=0,
                     warm_start=False)


In [25]:
shinkasen_rf = create_model('rf')

Accuracy     AUC  Recall   Prec.      F1   Kappa     MCC
0       0.8831  0.9566  0.8858  0.8977  0.8917  0.7648  0.7648
1       0.8905  0.9611  0.8904  0.9063  0.8983  0.7797  0.7798
2       0.8888  0.9585  0.8984  0.8970  0.8977  0.7759  0.7759
3       0.8787  0.9531  0.8796  0.8953  0.8874  0.7560  0.7562
4       0.8920  0.9592  0.8944  0.9056  0.9000  0.7826  0.7827
5       0.8816  0.9535  0.8851  0.8957  0.8904  0.7616  0.7617
6       0.8913  0.9605  0.8876  0.9101  0.8987  0.7815  0.7818
7       0.8928  0.9603  0.8944  0.9070  0.9007  0.7843  0.7844
8       0.8933  0.9606  0.8956  0.9068  0.9012  0.7853  0.7854
9       0.8958  0.9613  0.8894  0.9163  0.9027  0.7907  0.7911
Mean    0.8888  0.9585  0.8901  0.9038  0.8969  0.7762  0.7764
SD      0.0054  0.0029  0.0055  0.0067  0.0049  0.0109  0.0110

In [26]:
shinkasen_knn = create_model('knn')

Accuracy     AUC  Recall   Prec.      F1   Kappa     MCC
0       0.8731  0.9432  0.8898  0.8781  0.8839  0.7439  0.7440
1       0.8907  0.9501  0.8975  0.9008  0.8992  0.7798  0.7798
2       0.8836  0.9445  0.8941  0.8919  0.8930  0.7654  0.7654
3       0.8767  0.9372  0.8845  0.8881  0.8863  0.7517  0.7517
4       0.8829  0.9459  0.8885  0.8952  0.8919  0.7642  0.7643
5       0.8797  0.9413  0.8870  0.8911  0.8891  0.7578  0.7578
6       0.8812  0.9462  0.8839  0.8961  0.8900  0.7610  0.7611
7       0.8864  0.9482  0.9000  0.8920  0.8960  0.7710  0.7710
8       0.8858  0.9471  0.8919  0.8972  0.8945  0.7700  0.7700
9       0.8927  0.9491  0.8996  0.9024  0.9010  0.7838  0.7838
Mean    0.8833  0.9453  0.8917  0.8933  0.8925  0.7648  0.7649
SD      0.0057  0.0037  0.0056  0.0066  0.0051  0.0115  0.0115

In [27]:
shinkasen_lightgbm = create_model('lightgbm')

Accuracy     AUC  Recall   Prec.      F1   Kappa     MCC
0       0.8736  0.9500  0.8839  0.8834  0.8836  0.7452  0.7452
1       0.8829  0.9555  0.8889  0.8949  0.8919  0.7643  0.7643
2       0.8764  0.9528  0.8870  0.8856  0.8863  0.7509  0.7509
3       0.8685  0.9470  0.8672  0.8881  0.8775  0.7356  0.7358
4       0.8816  0.9552  0.8845  0.8962  0.8903  0.7617  0.7617
5       0.8705  0.9465  0.8728  0.8870  0.8799  0.7395  0.7396
6       0.8858  0.9563  0.8889  0.8997  0.8942  0.7701  0.7702
7       0.8802  0.9548  0.8867  0.8922  0.8894  0.7588  0.7588
8       0.8811  0.9551  0.8802  0.8988  0.8894  0.7608  0.7610
9       0.8891  0.9560  0.8854  0.9081  0.8966  0.7771  0.7774
Mean    0.8790  0.9529  0.8825  0.8934  0.8879  0.7564  0.7565
SD      0.0063  0.0035  0.0068  0.0073  0.0058  0.0127  0.0127

In [32]:
shinkasen_tuned_et = tune_model(shinkasen_et)

Accuracy     AUC  Recall   Prec.      F1   Kappa     MCC
0       0.8942  0.9578  0.8826  0.9193  0.9005  0.7877  0.7884
1       0.8972  0.9597  0.8875  0.9202  0.9036  0.7936  0.7942
2       0.8945  0.9594  0.8887  0.9145  0.9014  0.7881  0.7884
3       0.8955  0.9609  0.8825  0.9215  0.9016  0.7903  0.7911
4       0.8947  0.9584  0.8863  0.9168  0.9013  0.7885  0.7890
5       0.8931  0.9574  0.8722  0.9264  0.8985  0.7858  0.7874
6       0.8963  0.9603  0.8875  0.9185  0.9028  0.7917  0.7922
7       0.8899  0.9571  0.8840  0.9105  0.8971  0.7788  0.7792
8       0.8939  0.9581  0.8790  0.9218  0.8999  0.7871  0.7881
9       0.9044  0.9656  0.8893  0.9314  0.9099  0.8082  0.8092
Mean    0.8954  0.9595  0.8840  0.9201  0.9017  0.7900  0.7907
SD      0.0035  0.0024  0.0050  0.0056  0.0033  0.0071  0.0072

In [ ]:
hr_tuned_lightgbm = tune_model(hr_lightgbm)

Accuracy     AUC  Recall   Prec.      F1   Kappa     MCC
0       0.9280  0.9592  0.8247  0.9091  0.8649  0.8159  0.8177
1       0.9539  0.9788  0.8660  0.9655  0.9130  0.8818  0.8842
2       0.9424  0.9795  0.8969  0.8969  0.8969  0.8569  0.8569
3       0.9395  0.9668  0.8454  0.9318  0.8865  0.8454  0.8472
4       0.9510  0.9850  0.8763  0.9444  0.9091  0.8756  0.8768
5       0.9249  0.9557  0.7938  0.9277  0.8556  0.8052  0.8097
6       0.9509  0.9757  0.8958  0.9247  0.9101  0.8763  0.8765
7       0.9220  0.9723  0.8125  0.8966  0.8525  0.7996  0.8014
8       0.9220  0.9462  0.8646  0.8557  0.8601  0.8060  0.8060
9       0.9306  0.9690  0.8750  0.8750  0.8750  0.8270  0.8270
Mean    0.9365  0.9688  0.8551  0.9127  0.8824  0.8390  0.8403
SD      0.0120  0.0115  0.0332  0.0312  0.0226  0.0306  0.0303

In [ ]:
hr_tuned_rf = tune_model(hr_rf)

Accuracy     AUC  Recall   Prec.      F1   Kappa     MCC
0       0.7752  0.7850  0.5155  0.6173  0.5618  0.4123  0.4153
1       0.8213  0.8091  0.5155  0.7692  0.6173  0.5066  0.5239
2       0.7983  0.8078  0.4330  0.7368  0.5455  0.4269  0.4518
3       0.8184  0.7996  0.4639  0.8036  0.5882  0.4823  0.5122
4       0.8156  0.8080  0.5464  0.7260  0.6235  0.5046  0.5135
5       0.8035  0.7954  0.4639  0.7377  0.5696  0.4507  0.4711
6       0.8035  0.8384  0.4271  0.7593  0.5467  0.4335  0.4627
7       0.7977  0.8189  0.5417  0.6667  0.5977  0.4645  0.4690
8       0.7890  0.7624  0.3958  0.7170  0.5101  0.3896  0.4175
9       0.7977  0.7886  0.4583  0.7097  0.5570  0.4336  0.4510
Mean    0.8020  0.8013  0.4761  0.7243  0.5717  0.4505  0.4688
SD      0.0133  0.0195  0.0486  0.0499  0.0334  0.0369  0.0361

In [29]:
evaluate_model(shinkasen_tuned_et)

interactive(children=(ToggleButtons(description='Plot Type:', icons=('',), options=(('Hyperparameters', 'param…

In [ ]:
evaluate_model(hr_tuned_lightgbm)

interactive(children=(ToggleButtons(description='Plot Type:', icons=('',), options=(('Hyperparameters', 'param…

In [ ]:
evaluate_model(hr_tuned_rf)

interactive(children=(ToggleButtons(description='Plot Type:', icons=('',), options=(('Hyperparameters', 'param…

In [33]:
predict_model(shinkasen_tuned_et);

Model  Accuracy     AUC  ...      F1   Kappa     MCC
0  Extra Trees Classifier      0.88  0.9529  ...  0.8866  0.7594  0.7618

[1 rows x 8 columns]

In [ ]:
predict_model(hr_tuned_lightgbm);

Model  Accuracy     AUC  ...      F1   Kappa     MCC
0  Light Gradient Boosting Machine    0.9557  0.9827  ...  0.9218  0.8909  0.8909

[1 rows x 8 columns]

In [ ]:
predict_model(hr_tuned_rf);

Model  Accuracy     AUC  ...      F1   Kappa     MCC
0  Random Forest Classifier    0.8098  0.8192  ...  0.5974  0.4794  0.4963

[1 rows x 8 columns]

In [20]:
shinkasen_final_model = finalize_model(shinkasen_tuned_et)

In [21]:
save_model(shinkasen_final_model,'Final ET Model 20Feb2022')

Transformation Pipeline and Model Successfully Saved


(Pipeline(memory=None,
          steps=[('dtypes',
                  DataTypes_Auto_infer(categorical_features=[],
                                       display_types=True,
                                       features_todrop=['ID'], id_columns=['ID'],
                                       ml_usecase='classification',
                                       numerical_features=[],
                                       target='Overall_Experience',
                                       time_features=[])),
                 ('imputer',
                  Simple_Imputer(categorical_strategy='most frequent',
                                 fill_value_categorical=None,
                                 fill_value_numerical...
                  ExtraTreesClassifier(bootstrap=False, ccp_alpha=0.0,
                                       class_weight='balanced_subsample',
                                       criterion='gini', max_depth=6,
                                       max_features='

In [22]:
print(shinkasen_final_model)

ExtraTreesClassifier(bootstrap=False, ccp_alpha=0.0,
                     class_weight='balanced_subsample', criterion='gini',
                     max_depth=6, max_features='log2', max_leaf_nodes=None,
                     max_samples=None, min_impurity_decrease=0.001,
                     min_impurity_split=None, min_samples_leaf=6,
                     min_samples_split=9, min_weight_fraction_leaf=0.0,
                     n_estimators=190, n_jobs=-1, oob_score=False,
                     random_state=123, verbose=0, warm_start=False)


In [34]:
unseen_predictions = predict_model(shinkasen_tuned_et, data=data_unseen)
unseen_predictions.head()

ID  Gender       CustomerType  ...  Online_boarding Label   Score
0  99900001  Female                NaN  ...             poor     1  0.8336
1  99900002  Female  disloyal Customer  ...       acceptable     0  0.6317
2  99900003    Male     Loyal Customer  ...        excellent     1  0.8104
3  99900004  Female     Loyal Customer  ...             poor     0  0.6846
4  99900005    Male  disloyal Customer  ...        excellent     1  0.7889

[5 rows x 26 columns]

In [35]:
test_prediction = unseen_predictions.copy()
test_prediction.head()

ID  Gender       CustomerType  ...  Online_boarding Label   Score
0  99900001  Female                NaN  ...             poor     1  0.8336
1  99900002  Female  disloyal Customer  ...       acceptable     0  0.6317
2  99900003    Male     Loyal Customer  ...        excellent     1  0.8104
3  99900004  Female     Loyal Customer  ...             poor     0  0.6846
4  99900005    Male  disloyal Customer  ...        excellent     1  0.7889

[5 rows x 26 columns]

In [36]:
test_prediction.rename(columns = {'Label':'Overall_Experience'}, inplace = True)
test_prediction.head()

ID  Gender  ... Overall_Experience   Score
0  99900001  Female  ...                  1  0.8336
1  99900002  Female  ...                  0  0.6317
2  99900003    Male  ...                  1  0.8104
3  99900004  Female  ...                  0  0.6846
4  99900005    Male  ...                  1  0.7889

[5 rows x 26 columns]

In [37]:
submission = test_prediction[['ID','Overall_Experience']]
submission.head()

ID  Overall_Experience
0  99900001                   1
1  99900002                   0
2  99900003                   1
3  99900004                   0
4  99900005                   1

In [38]:
submission_csv = submission.to_csv('submission.csv', index=False)

In [ ]:
save_model(hr_final_model,'HR_Attrition_Final_Lightgbm_Model_16Feb2022')

Transformation Pipeline and Model Successfully Saved


(Pipeline(memory=None,
          steps=[('dtypes',
                  DataTypes_Auto_infer(categorical_features=[],
                                       display_types=True, features_todrop=[],
                                       id_columns=[],
                                       ml_usecase='classification',
                                       numerical_features=[], target='Attrition',
                                       time_features=[])),
                 ('imputer',
                  Simple_Imputer(categorical_strategy='not_available',
                                 fill_value_categorical=None,
                                 fill_value_numerical=None,
                                 numeric_st...
                                 colsample_bytree=1.0, feature_fraction=0.5,
                                 importance_type='split', learning_rate=0.4,
                                 max_depth=-1, min_child_samples=6,
                                 min_child_weight=0.

In [ ]:
# saved_final_rf = load_model('Final RF Model 11Nov2020')

In [ ]:
#new_prediction = predict_model(saved_final_rf, data=data_unseen)
#new_prediction.head()